## Задание 1

### 1) В среде Google Colab создали новый блокнот (notebook). Импортировали необходимые для работы библиотеки и модули.

In [ ]:
# импорт модулей
import os
os.chdir('/content/drive/MyDrive/Colab Notebooks/is_lab2')

import numpy as np
import lab02_lib as lib

### 2) Сгенерировали индивидуальный набор двумерных данных в пространстве признаков с координатами центра (6, 6), где 6 – номер бригады. Вывели полученные данные на рисунок и в консоль.

In [ ]:
# генерация датасета
data = lib.datagen(6, 6, 1000, 2)

# вывод данных и размерности
print('Исходные данные:')
print(data)
print('Размерность данных:')
print(data.shape)

### 3) Создали и обучили автокодировщик AE1 простой архитектуры, выбрав небольшое количество эпох обучения. Зафиксировали в таблице вида табл.1 количество скрытых слоёв и нейронов в них

In [ ]:
# обучение AE1
patience = 300
ae1_trained, IRE1, IREth1 = lib.create_fit_save_ae(data,'out/AE1.h5','out/AE1_ire_th.txt',
1000, True, patience)

### 4) Зафиксировали ошибку MSE, на которой обучение завершилось. Построили график ошибки реконструкции обучающей выборки. Зафиксировали порог ошибки реконструкции – порог обнаружения аномалий.

Ошибка MSE_AE1 = 19.5568

In [ ]:
# Построение графика ошибки реконструкции
lib.ire_plot('training', IRE1, IREth1, 'AE1')

### 5) Создали и обучили второй автокодировщик AE2 с усложненной архитектурой, задав большее количество эпох обучения

In [ ]:
# обучение AE2
ae2_trained, IRE2, IREth2 = lib.create_fit_save_ae(data,'out/AE2.h5','out/AE2_ire_th.txt',
3000, True, patience)

### 6) Зафиксировали ошибку MSE, на которой обучение завершилось. Построили график ошибки реконструкции обучающей выборки. Зафиксировали второй порог ошибки реконструкции – порог обнаружения аномалий.

Ошибка MSE_AE2 = 0.0108

In [ ]:
# Построение графика ошибки реконструкции
lib.ire_plot('training', IRE2, IREth2, 'AE2')

### 7) Рассчитали характеристики качества обучения EDCA для AE1 и AE2. Визуализировали и сравнили области пространства признаков, распознаваемые автокодировщиками AE1 и AE2. Сделали вывод о пригодности AE1 и AE2 для качественного обнаружения аномалий.


In [ ]:
# построение областей покрытия и границ классов
# расчет характеристик качества обучения
numb_square = 20
xx, yy, Z1 = lib.square_calc(numb_square, data, ae1_trained, IREth1, '1', True)

In [ ]:
# построение областей покрытия и границ классов
# расчет характеристик качества обучения
numb_square = 20
xx, yy, Z2 = lib.square_calc(numb_square, data, ae2_trained, IREth2, '2', True)

In [ ]:
# сравнение характеристик качества обучения и областей аппроксимации
lib.plot2in1(data, xx, yy, Z1, Z2)

### 8) Если автокодировщик AE2 недостаточно точно аппроксимирует область обучающих данных, то подобрать подходящие параметры автокодировщика и повторить шаги (6) – (8).

Полученные показатели EDCA для автокодировщика AE2 нас устраивают.

### 9) Изучили сохраненный набор данных и пространство признаков. Создали тестовую выборку, состоящую, как минимум, из 4ёх элементов, не входящих в обучающую выборку. Элементы должны быть такими, чтобы AE1 распознавал их как норму, а AE2 детектировал как аномалии.

In [ ]:
# загрузка тестового набора
data_test = np.loadtxt('data_test.txt', dtype=float)
print(data_test)

### 10) Применили обученные автокодировщики AE1 и AE2 к тестовым данным и вывели значения ошибки реконструкции для каждого элемента тестовой выборки относительно порога на график и в консоль.

In [ ]:
# тестирование АE1
predicted_labels1, ire1 = lib.predict_ae(ae1_trained, data_test, IREth1)

In [ ]:
# тестирование АE1
lib.anomaly_detection_ae(predicted_labels1, ire1, IREth1)
lib.ire_plot('test', ire1, IREth1, 'AE1')

In [ ]:
# тестирование АE2
predicted_labels2, ire2 = lib.predict_ae(ae2_trained, data_test, IREth2)

In [ ]:
# тестирование АE2
lib.anomaly_detection_ae(predicted_labels2, ire2, IREth2)
lib.ire_plot('test', ire2, IREth2, 'AE2')

### 11) Визуализировали элементы обучающей и тестовой выборки в областях пространства признаков, распознаваемых автокодировщиками AE1 и AE2.

In [ ]:
# построение областей аппроксимации и точек тестового набора
lib.plot2in1_anomaly(data, xx, yy, Z1, Z2, data_test)

### 12) Результаты исследования занесли в таблицу:
Табл. 1 Результаты задания №1

|      | Количество<br>скрытых слоев | Количество<br>нейронов в скрытых слоях | Количество<br>эпох обучения | Ошибка<br>MSE_stop | Порог ошибки<br>реконструкции | Значение показателя<br>Excess | Значение показателя<br>Approx | Количество обнаруженных<br>аномалий |
|-----:|------------------------------|----------------------------------------|-----------------------------|--------------------|-------------------------------|-------------------------------|--------------------------------|-------------------------------------|
| AE1  | 1                            | 1                            | 1000                        | 19.5568             | 6.53                         | 12.67                          | 0.073                           | 0                                   |
| AE2  | 5                            | 3,2,1,2,3                                | 3000                          | 0.0108             | 0.4                         | 0.33                          | 0.750                           | 4                                   |


### 13) Сделали выводы о требованиях к:
- данным для обучения,
- архитектуре автокодировщика,
- количеству эпох обучения,
- ошибке MSE_stop, приемлемой для останова обучения,
- ошибке реконструкции обучающей выборки (порогу обнаружения
аномалий),
- характеристикам качества обучения EDCA одноклассового
классификатора

для качественного обнаружения аномалий в данных.

1) Данные для обучения должны быть без аномалий, чтобы автокодировщик смог рассчитать верное пороговое значение
2) Архитектура автокодировщика должна постепенно сужатся к бутылочному горлышку,а затем постепенно возвращатся к исходным выходным размерам, кол-во скрытых слоев 3-5
3) В рамках данного набора данных оптимальное кол-во эпох 3000 с patience 300 эпох
4) Оптимальная ошибка MSE-stop в районе 0.01, желательно не меньше для предотвращения переобучения
5) Значение порога в районе 0.4
6) Значение Excess не больше 0.5, значение Deficit равное 0, значение Coating равное 1, значение Approx не меньше 0.7

## Задание 2

### 1) Изучить описание своего набора реальных данных, что он из себя представляет

Бригада 6 => набор данных Cardio. Это реальный набор данных, который состоит из измерений частоты сердечных сокращений плода и
сокращений матки на кардиотокограммах, классифицированных экспертами
акушерами. Исходный набор данных предназначен для классификации. В нем
представлено 3 класса: «норма», «подозрение» и «патология». Для обнаружения
аномалий класс «норма» принимается за норму, класс «патология» принимается за
аномалии, а класс «подозрение» был отброшен.

| Количество<br>признаков | Количество<br>примеров | Количество<br>нормальных примеров | Количество<br>аномальных примеров |
|-------------------------:|-----------------------:|----------------------------------:|-----------------------------------:|
| 21                       | 1764                   | 1655                               | 109                                |


### 2) Загрузить многомерную обучающую выборку реальных данных Cardio.txt.

In [ ]:
# загрузка обчуающей выборки
train = np.loadtxt('data/cardio_train.txt', dtype=float)

### 3) Вывести полученные данные и их размерность в консоли.

In [ ]:
print('train:\n', train)
print('train.shape:', np.shape(train))

### 4) Создать и обучить автокодировщик с подходящей для данных архитектурой. Выбрать необходимое количество эпох обучения.

In [ ]:
# **kwargs
# verbose_every_n_epochs - отображать прогресс каждые N эпох (по умолчанию - 1000)
# early_stopping_delta - дельта для ранней остановки (по умолчанию - 0.01)
# early_stopping_value = значение для ранней остановки (по умолчанию -  0.0001)

from time import time

patience = 4000
start = time()
ae3_v1_trained, IRE3_v1, IREth3_v1 = lib.create_fit_save_ae(train,'out/AE3_V1.h5','out/AE3_v1_ire_th.txt',
100000, False, patience, early_stopping_delta = 0.001)
print("Время на обучение: ", time() - start)

### 5) Зафиксировать ошибку MSE, на которой обучение завершилось. Построить график ошибки реконструкции обучающей выборки. Зафиксировать порог ошибки реконструкции – порог обнаружения аномалий.

Скрытых слоев 7, нейроны: 46->26->14->10->14->26->48

Ошибка MSE_AE3_v1 = 0.0126

In [ ]:
# Построение графика ошибки реконструкции
lib.ire_plot('training', IRE3_v1, IREth3_v1, 'AE3_v1')

### 6) Сделать вывод о пригодности обученного автокодировщика для качественного обнаружения аномалий. Если порог ошибки реконструкции слишком велик, то подобрать подходящие параметры автокодировщика и повторить шаги (4) – (6).

In [ ]:
# **kwargs
# verbose_every_n_epochs - отображать прогресс каждые N эпох (по умолчанию - 1000)
# early_stopping_delta - дельта для ранней остановки (по умолчанию - 0.01)
# early_stopping_value = значение для ранней остановки (по умолчанию -  0.0001)

from time import time

patience = 4000
start = time()
ae3_v2_trained, IRE3_v2, IREth3_v2 = lib.create_fit_save_ae(train,'out/AE3_V2.h5','out/AE3_v2_ire_th.txt',
100000, False, patience, early_stopping_delta = 0.001)
print("Время на обучение: ", time() - start)

Скрытых слоев 7, нейроны: 48->36->28->22->16->12->16->22->28->36->48

Ошибка MSE_AE3_v1 = 0.0098

In [ ]:
# Построение графика ошибки реконструкции
lib.ire_plot('training', IRE3_v2, IREth3_v2, 'AE3_v2')

### 7) Изучить и загрузить тестовую выборку Cardio.txt.

In [ ]:
#загрузка тестовой выборки
test = np.loadtxt('data/cardio_test.txt', dtype=float)
print('\n test:\n', test)
print('test.shape:', np.shape(test))

### 8) Подать тестовую выборку на вход обученного автокодировщика для обнаружения аномалий. Вывести график ошибки реконструкции элементов тестовой выборки относительно порога.

In [ ]:
# тестирование АE3
predicted_labels3_v1, ire3_v1 = lib.predict_ae(ae3_v1_trained, test, IREth3_v1)

In [ ]:
# Построение графика ошибки реконструкции
lib.ire_plot('test', ire3_v1, IREth3_v1, 'AE3_v1')

In [ ]:
# тестирование АE3
predicted_labels3_v2, ire3_v2 = lib.predict_ae(ae3_v2_trained, test, IREth3_v2)

In [ ]:
# Построение графика ошибки реконструкции
lib.ire_plot('test', ire3_v2, IREth3_v2, 'AE3_v2')

In [ ]:
# тестирование АE2
lib.anomaly_detection_ae(predicted_labels3_v1, IRE3_v1, IREth3_v1)

Для AE3_v1 точность составляет 88%

In [ ]:
# тестирование АE2
lib.anomaly_detection_ae(predicted_labels3_v2, IRE3_v2, IREth3_v2)

Для AE3_v2 точность составляет 92%

### 9) Если результаты обнаружения аномалий не удовлетворительные (обнаружено менее 70% аномалий), то подобрать подходящие параметры автокодировщика и повторить шаги (4) – (9).

Результаты обнаружения аномалий удовлетворены.

### 10) Параметры наилучшего автокодировщика и результаты обнаружения аномалий занести в таблицу:
Табл. 2 Результаты задания №2

| Dataset name | Количество<br>скрытых слоев | Количество<br>нейронов в скрытых слоях | Количество<br>эпох обучения | Ошибка<br>MSE_stop | Порог ошибки<br>реконструкции | % обнаруженных<br>аномалий |
|:-------------|:-----------------------------|:----------------------------------------|:-----------------------------|:-------------------|:-------------------------------|:---------------------------|
| Cardio       | 11                             | 48, 36, 28, 22, 16, 10, 16, 22, 28, 36, 48              | 100000                      | 0.0098              | 1.6                           | 92%                      |


### 11) Сделать выводы о требованиях к:
- данным для обучения,
- архитектуре автокодировщика,  
- количеству эпох обучения,
- ошибке MSE_stop, приемлемой для останова обучения,
- ошибке реконструкции обучающей выборки (порогу обнаружения
аномалий)

для качественного обнаружения аномалий в случае, когда размерность
пространства признаков высока.

1) Данные для обучения должны быть без аномалий, чтобы автокодировщик смог рассчитать верное пороговое значение
2) Архитектура автокодировщика должна постепенно сужатся к бутылочному горлышку,а затем постепенно возвращатся к исходным выходным размерам, кол-во скрытых слоев 7-11.
3) В рамках данного набора данных оптимальное кол-во эпох 100000 с patience 4000 эпох
4) Оптимальная ошибка MSE-stop в районе 0.001, желательно не меньше для предотвращения переобучения
5) Значение порога не больше 1.6